In [353]:
import pandas as pd
import re
import nltk
from nltk.tokenize import sent_tokenize, word_tokenize
from pymorphy3 import MorphAnalyzer
from nltk.corpus import stopwords
import numpy as np
import torch.nn as nn
from sklearn.model_selection import train_test_split
import torch
from sklearn.model_selection import train_test_split
from torch.utils.data import TensorDataset, DataLoader

In [354]:
stopwords = stopwords.words('russian')

In [355]:
df = pd.read_csv('./data/Petitions.csv')
df

id                               public_petition_text  \
0      3168490                                     снег на дороге   
1      3219678                очистить кабельный киоск от рекламы   
2      2963920  Просим убрать все деревья и кустарники, которы...   
3      3374910  Неудовлетворительное состояние парадной - надп...   
4      3336285                                           Граффити   
...        ...                                                ...   
59884  3128111                           прошу закрасить граффити   
59885  3276713       Прошу вас отремонтировать пешеходную дорожку   
59886  3274663  Необходимо демонтировать незаконную рекламную ...   
59887  3359308  Очень гремит на ветру металлическая часть окна...   
59888  3209098  Две проблемы в одном:\n1) Незаконные надписи/о...   

                                         reason_category  
0                                        Благоустройство  
1                                        Благоустройство  
2                                        Благоустройство  
3                                         Содержание МКД  
4                                        Благоустройство  
...                                                  ...  
59884                                    Благоустройство  
59885                                    Благоустройство  
59886  Незаконная информационная и (или) рекламная ко...  
59887                                             Кровля  
59888                                    Благоустройство  

[59889 rows x 3 columns]

In [356]:
print(len(df['reason_category'].unique()), "\n", df['reason_category'].value_counts())

15 
 reason_category
Благоустройство                                                                     34769
Содержание МКД                                                                      14461
Нарушение правил пользования общим имуществом                                        2170
Незаконная информационная и (или) рекламная конструкция                              1831
Фасад                                                                                1483
Повреждения или неисправность элементов уличной инфраструктуры                       1164
Кровля                                                                                825
Водоснабжение                                                                         809
Состояние рекламных или информационных конструкций                                    673
Санитарное состояние                                                                  434
Центральное отопление                                                          

In [357]:
df.drop(columns="id", inplace=True)

In [358]:
new_df = df.sample(100)
new_df

public_petition_text  \
16847                                   Мусор на газонах   
22038                   Просьба стереть надписи. Спасибо   
37739  Сломана одна из табличек с номером этажа на 16...   
26142                                              Мусор   
42695       Мусор на тротуаре. 12-Красноармейская дом 35   
...                                                  ...   
59699  Гражданский 75-1,  третья парадная.  Прошу про...   
1596   По адресу проспект Авиаконструкторов дом 6, не...   
32550                                    починить фонарь   
100                          Рекламный щит весь исписан.   
57955             Повреждены почтовые ящики. 4 парадная.   

                                         reason_category  
16847                                    Благоустройство  
22038                                    Благоустройство  
37739                                     Содержание МКД  
26142                                    Благоустройство  
42695                                    Благоустройство  
...                                                  ...  
59699                                     Содержание МКД  
1596                                              Кровля  
32550                                    Благоустройство  
100    Состояние рекламных или информационных констру...  
57955                                     Содержание МКД  

[100 rows x 2 columns]

In [359]:
X = new_df["public_petition_text"].to_list()
y = new_df["reason_category"].to_list()

In [360]:
text1 = ['<p> Привет, чурка! Также Я: любл%ю тебя; и был @$, но не ты дурак</p>', 'Привет, чурка, я в Дубае']

In [361]:
# html_tag=re.compile('<.*?>')
# text = html_tag.sub('', text)
# text

In [362]:
def preprocessing_text(text):
    lst = []
    #remove html
    for i in text:
        html_tag=re.compile('<.*?>')
        text_no_html = html_tag.sub('', i)
        #remove quots
        text_only_letters = re.sub('[^\w\s]', '', text_no_html)
        #tokenizим
        words = word_tokenize(text_only_letters)
        #morphим
        morph = MorphAnalyzer()
        lemmas = [morph.normal_forms(w)[0] for w in words]
        #del_sw
        prepared = [w for w in lemmas if w not in stopwords]
        lemm_sentce = ' '.join(prepared)
        lst.append(lemm_sentce)
        # lst.append(prepared)
    return lst


In [363]:
prepro_text = preprocessing_text(text=X)
print(len(prepro_text))
prepro_text

100


['мусор газон',
 'просьба стереть надпись спасибо',
 'сломать табличка номер этаж 16 этаж первый парадный',
 'мусор',
 'мусор тротуар 12красноармейский дом 35',
 'гореть светильник уличный фонарь',
 'вблизи здание поселковый улица 2с3 направление помелкова 18б находчться небольшой удаление друг друг 6 7 высохший трухлявый берёза который сильный ветер качать нужно убрать',
 'трещина место сварка соединять дверь петля верхний 18 этаж 1 подъезд',
 '5 парадный 1 этаж выход парадный нарушение тепловой контур район ручка входной дверь выгнутый полотно задувать воздух улица теплопотеря моп стоить свист постоянный изз деформация полотно',
 'жкс3 обязать ежедневно убирать внутридворовый территория это взимать значительный денежный средство каждый собственник однако вместо это жкс3 течение 15 месяц территория дом 26 28 пр наука сторона далее 28 организовать свалка мусор свой бездействие невыполнение обязательный ежедневный уборка территория превратить часть газон помойка никто жкс3 администрация

In [364]:
def del_word_len_one(list_w):
    w_del = []
    for i in range(0, len(list_w)):
        if len(list_w[i].split()) < 3:
            w_del.append(i)
    for index in sorted(w_del, reverse=True):
        del list_w[index]
        
    return list_w

In [365]:
new_prepro_text = del_word_len_one(prepro_text)
new_prepro_text

['просьба стереть надпись спасибо',
 'сломать табличка номер этаж 16 этаж первый парадный',
 'мусор тротуар 12красноармейский дом 35',
 'гореть светильник уличный фонарь',
 'вблизи здание поселковый улица 2с3 направление помелкова 18б находчться небольшой удаление друг друг 6 7 высохший трухлявый берёза который сильный ветер качать нужно убрать',
 'трещина место сварка соединять дверь петля верхний 18 этаж 1 подъезд',
 '5 парадный 1 этаж выход парадный нарушение тепловой контур район ручка входной дверь выгнутый полотно задувать воздух улица теплопотеря моп стоить свист постоянный изз деформация полотно',
 'жкс3 обязать ежедневно убирать внутридворовый территория это взимать значительный денежный средство каждый собственник однако вместо это жкс3 течение 15 месяц территория дом 26 28 пр наука сторона далее 28 организовать свалка мусор свой бездействие невыполнение обязательный ежедневный уборка территория превратить часть газон помойка никто жкс3 администрация район абсолютно волновать

In [366]:
count_vocab = set((' '.join(new_prepro_text).split()))
word_to_ix = {word: i for i, word in enumerate(count_vocab)}
word_to_ix

{'горячий': 0,
 'партизан': 1,
 'автоматически': 2,
 'травма': 3,
 'электрощит': 4,
 'жительство': 5,
 'режим': 6,
 'ужасный': 7,
 'мера': 8,
 '408': 9,
 'дефект': 10,
 'вообще': 11,
 'подъём': 12,
 'повредить': 13,
 'голый': 14,
 'остаться': 15,
 'пятьдесят': 16,
 'открываться': 17,
 'лифтовый': 18,
 'должностной': 19,
 'работать': 20,
 'план': 21,
 'внутридворовый': 22,
 'тяжело': 23,
 'требоваться': 24,
 'таракан': 25,
 'становиться': 26,
 'асфальт': 27,
 'элемент': 28,
 'помошить': 29,
 'к9': 30,
 'тяжёлый': 31,
 'заменить': 32,
 'помойка': 33,
 'выкидывать': 34,
 'тротуар': 35,
 'принести': 36,
 'состояние': 37,
 'трамвай': 38,
 'пустой': 39,
 'пять': 40,
 'часть': 41,
 'третий': 42,
 'уважаемый': 43,
 'запах': 44,
 'урна': 45,
 'какойтый': 46,
 '15': 47,
 'иметься': 48,
 'ближний': 49,
 'незаконный': 50,
 'кабельканал': 51,
 'строка': 52,
 'требовать': 53,
 'моп': 54,
 'доводчик': 55,
 'который': 56,
 'замок': 57,
 'особенно': 58,
 'бордель': 59,
 'неисправность': 60,
 'рф': 61,


In [367]:
def get_context_words(data, m):
    central_words = []
    context_words = []
    s = []
    for k in range(0, len(data)):
        for i in range(m, (len(data[k].split()) - (m * 2)) + (m)):
            # print(i)
            central_word = data[k].split()[i]
            central_words.append(word_to_ix[central_word])

            context_word = []
            for j in range(i - m, i + m + 1):
                if j != i:
                    context_word.append(word_to_ix[data[k].split()[j]])
            context_words.append(context_word)

    s = list(zip(central_words, context_words))

    return s

In [368]:
s = get_context_words(new_prepro_text, m=1)

In [369]:
s

[(559, [236, 454]),
 (454, [559, 68]),
 (159, [197, 226]),
 (226, [159, 540]),
 (540, [226, 292]),
 (292, [540, 540]),
 (540, [292, 365]),
 (365, [540, 88]),
 (35, [488, 93]),
 (93, [35, 515]),
 (515, [93, 575]),
 (202, [587, 263]),
 (263, [202, 354]),
 (591, [238, 554]),
 (554, [591, 500]),
 (500, [554, 459]),
 (459, [500, 614]),
 (614, [459, 334]),
 (334, [614, 399]),
 (399, [334, 510]),
 (510, [399, 451]),
 (451, [510, 409]),
 (409, [451, 65]),
 (65, [409, 65]),
 (65, [65, 79]),
 (79, [65, 425]),
 (425, [79, 107]),
 (107, [425, 600]),
 (600, [107, 241]),
 (241, [600, 56]),
 (56, [241, 527]),
 (527, [56, 544]),
 (544, [527, 158]),
 (158, [544, 497]),
 (497, [158, 611]),
 (426, [101, 635]),
 (635, [426, 269]),
 (269, [635, 339]),
 (339, [269, 384]),
 (384, [339, 228]),
 (228, [384, 439]),
 (439, [228, 540]),
 (540, [439, 284]),
 (284, [540, 294]),
 (88, [201, 284]),
 (284, [88, 540]),
 (540, [284, 203]),
 (203, [540, 88]),
 (88, [203, 388]),
 (388, [88, 523]),
 (523, [388, 414]),
 (41

In [370]:
word_list = s[0][1]
word_list

[236, 454]

In [371]:
# with open('word_list3.tsv', 'w', encoding='utf-8') as f:
#     f.write('\n'.join(word_list))

In [372]:
def embedding_matrix(f):
    count_vocab = set((' '.join(f).split()))
    print(len(count_vocab))
    word_to_ix = {word: i for i, word in enumerate(count_vocab)}
    print(word_to_ix)
    a = max(word_to_ix.values()) + 1
    print(a)
    matrica = [[0] * a for _ in range(a)]
    for k in range(0, len(f)):
        b = len(f[k].split())
        words = f[k].split()
        for i in range(b):
            for j in range(i+1, b):
                if words[i] in f[k] and words[j] in f[k]:
                    matrica[word_to_ix[words[i]]][word_to_ix[words[j]]] += 1
                    matrica[word_to_ix[words[j]]][word_to_ix[words[i]]] += 1

    # for row in matrica:
    #     print(row)
    
    return matrica

In [373]:
emb_matr = embedding_matrix(new_prepro_text)
emb_matr

663
{'горячий': 0, 'партизан': 1, 'автоматически': 2, 'травма': 3, 'электрощит': 4, 'жительство': 5, 'режим': 6, 'ужасный': 7, 'мера': 8, '408': 9, 'дефект': 10, 'вообще': 11, 'подъём': 12, 'повредить': 13, 'голый': 14, 'остаться': 15, 'пятьдесят': 16, 'открываться': 17, 'лифтовый': 18, 'должностной': 19, 'работать': 20, 'план': 21, 'внутридворовый': 22, 'тяжело': 23, 'требоваться': 24, 'таракан': 25, 'становиться': 26, 'асфальт': 27, 'элемент': 28, 'помошить': 29, 'к9': 30, 'тяжёлый': 31, 'заменить': 32, 'помойка': 33, 'выкидывать': 34, 'тротуар': 35, 'принести': 36, 'состояние': 37, 'трамвай': 38, 'пустой': 39, 'пять': 40, 'часть': 41, 'третий': 42, 'уважаемый': 43, 'запах': 44, 'урна': 45, 'какойтый': 46, '15': 47, 'иметься': 48, 'ближний': 49, 'незаконный': 50, 'кабельканал': 51, 'строка': 52, 'требовать': 53, 'моп': 54, 'доводчик': 55, 'который': 56, 'замок': 57, 'особенно': 58, 'бордель': 59, 'неисправность': 60, 'рф': 61, 'замусорить': 62, 'предпринимать': 63, 'теплопотеря': 64,

[[0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,


In [374]:
from sklearn.decomposition import PCA

In [375]:
pca = PCA(n_components=30)
pca.fit(emb_matr)
data_pca = pca.transform(emb_matr)

In [376]:
np.savetxt('embeddings.tsv', data_pca, delimiter='\t')

## Neural_buri

In [377]:
# [(256, [23, 45])
# (256, [23, 45])
# (256, [23, 45])]
X_i = np.array([])
y_i = np.array([])
for i, j in s:
    y_i = np.insert(y_i, 0, i)
    X_i = np.insert(X_i, 0, j).reshape(-1, 2)

In [378]:
y_i

array([283., 361., 655., ..., 159., 454., 559.])

In [379]:
X_i

array([[361.,  88.],
       [655., 283.],
       [ 13., 361.],
       ...,
       [197., 226.],
       [559.,  68.],
       [236., 454.]])

In [380]:
X_train, X_test, y_train, y_test = train_test_split(X_i, y_i, test_size=0.15)
X_train.shape, X_test.shape, y_train.shape, y_test.shape

((878, 2), (155, 2), (878,), (155,))

In [381]:
batch_size = 256
train_ds = TensorDataset(torch.from_numpy(X_train).type(torch.long), torch.from_numpy(y_train).type(torch.long))
train_dl = DataLoader(train_ds, batch_size=batch_size, shuffle=True)

In [382]:
import torch.nn.functional as F

In [390]:
class CBOWModeler(nn.Module):  
    def __init__(self, vocab_size, embedding_dim):
        super(CBOWModeler, self).__init__()
        self.embeddings = nn.Embedding(vocab_size, embedding_dim)
        self.linear1 = nn.Linear(embedding_dim, 250)
        self.linear2 = nn.Linear(250, vocab_size)

    def forward(self, inputs):
        embeds = self.embeddings(inputs)
        print(embeds.shape)
        out1 = F.tanh(self.linear1(embeds))
        out2 = self.linear2(out1)           
        log_probs = F.log_softmax(out2, dim=1)
        return log_probs
    

In [391]:
loss_function = nn.NLLLoss()

In [392]:
model = CBOWModeler(len(count_vocab), 10)
model

CBOWModeler(
  (embeddings): Embedding(663, 10)
  (linear1): Linear(in_features=10, out_features=250, bias=True)
  (linear2): Linear(in_features=250, out_features=663, bias=True)
)

In [393]:
optimizer = torch.optim.SGD(model.parameters(), lr=0.001)

In [394]:
wordvecs = model.linear2.weight.cpu().detach().numpy()
wordvecs

array([[-0.02998514,  0.03263452,  0.04025929, ..., -0.04683756,
         0.03547717,  0.03916381],
       [ 0.01203896, -0.04898686,  0.06278095, ...,  0.03732147,
        -0.04527028,  0.03980055],
       [-0.04450283, -0.03093316, -0.00321195, ..., -0.02661448,
         0.02101055, -0.05853667],
       ...,
       [-0.05413519, -0.03705012,  0.0518464 , ...,  0.04058658,
         0.04669289,  0.02028847],
       [ 0.00428952, -0.04486413, -0.03924589, ...,  0.01985881,
        -0.03725972,  0.00269806],
       [ 0.04657376,  0.0605051 ,  0.00149807, ...,  0.05621338,
        -0.01092984, -0.04692823]], dtype=float32)

In [395]:
np.savetxt('word2vec_vectors.tsv', wordvecs, delimiter='\t')

In [396]:
epochs = 5

loss_values = []
for epoch in range(epochs):
    for x_b, y_b in train_dl:

        outputs = model(x_b)
        print(outputs.shape)
        print(y_b.shape)
        loss_value = loss_function(outputs, y_b)

        loss_value.backward()

        optimizer.step()

        optimizer.zero_grad()
    loss_values.append(loss_value.item())

    print(f'Эпоха {epoch + 1}, Значение функции потерь: {loss_value.item()}')

torch.Size([256, 2, 10])
torch.Size([256, 2, 663])
torch.Size([256])


RuntimeError: Expected target size [256, 663], got [256]